# Asking Questions in Biblical Greek

This [Jupyter notebook](https://jupyter.org/) explores different ways to ask questions found in the Greek New Testament.

For more on this topic, please consult these references:

- [Interrogative Clauses](https://github.com/livingkoine/two-week-greek/blob/master/handouts/jannaris-questions.pdf) from *An Historical Greek Grammar* by A.N. Jannaris
- [Asking Questions in Biblical Greek](https://github.com/livingkoine/two-week-greek/blob/master/handouts/Asking%20Questions%20in%20Biblical%20Greek.pdf) by Jonathan Robie

In any Greek sentence shown, you can see an English gloss and morphology by letting your mouse rest over the word.  Some mobile devices do not display properly, use "request desktop website" or use a computer to view this if you run into that problem. 

The examples in this notebook are generated using queries, but feel free to ignore the queries themselves and focus on the examples.  The queries are written in [XQuery 3.1](https://www.w3.org/TR/xquery-31/) using the [greeksyntax module](http://jonathanrobie.biblicalhumanities.org/blog/2017/12/08/jupyter-tutorial/) and the [Nestle1904 Lowfat Treebank](https://github.com/biblicalhumanities/greek-new-testament/tree/master/syntax-trees/nestle1904-lowfat). The next cell opens the database that we will use for our queries.

In [1]:
from greeksyntax.lowfat import *

q = lowfat("nestle1904lowfat")

Database 'nestle1904lowfat' was opened in 16.89 ms.



## Overview

We want to start by looking at the frequency of questions and the various forms of questions.

There are many ways to ask a question in Greek, including:

- Interrogative pronouns
- Interrogative adjectives
- Interrogative adverbs
- Giving choices with ἢ
- Negation
- Tone of voice with no syntactic marker

Because of that, there is no single marker to query on, so we will use the question mark as a rough indicator, since most questions do have a question mark.  Not all do, some questions in indirect speech do not have a question mark, e.g.

> Matt.6.25 Διὰ τοῦτο λέγω ὑμῖν, μὴ μεριμνᾶτε τῇ ψυχῇ ὑμῶν τί φάγητε, ἢ τί πίητε μηδὲ τῷ σώματι ὑμῶν τί ἐνδύσησθε· 

In addition, a single sentence can have multiple question marks, e.g.

>  Matt.6.31 μὴ οὖν μεριμνήσητε λέγοντες· Τί φάγωμεν; ἤ· Τί πίωμεν; ἤ· Τί περιβαλώμεθα; 

Therefore, the counts in this section should be regarded as 100% accurate, and the examples shown in this section may not include some examples shown in later sections.


### How frequent are questions in the GNT?

How many question marks are there in the GNT?

In [2]:
q.count("//pc[.=';']")

How many periods are there in the GNT?

In [3]:
q.count("//pc[.='.']")

What are the punctuation marks in the GNT?

In [4]:
q.xquery("distinct-values(//pc)")

,
.
·
;


What percent of punctuation marks are question marks?

In [5]:
query = """
    let $total := count(//pc)
    for $pc in distinct-values(//pc)
    let $count := count(//pc[.=$pc])
    let $percent := 100 * ($count div $total)
    order by $count
    return ``[`{$pc}` count=`{$count}`, percent=`{format-number($percent, "#.###")}` ]``
"""

q.xquery(query)

; count=969, percent=5.244 
· count=2355, percent=12.746 
. count=5712, percent=30.914 
, count=9441, percent=51.096 


What percent of sentences are questions, as opposed to statements?

In [6]:
query = """
    let $final := //pc[. = (';', '.')]
    let $total := count($final)
    for $pc in distinct-values($final)
    let $count := count(//pc[.=$pc])
    let $percent := 100 * ($count div $total)
    order by $count
    return  ``[`{$pc}` count=`{$count}`, percent=`{format-number($percent, "#.###")}` ]``
"""

q.xquery(query)

; count=969, percent=14.504 
. count=5712, percent=85.496 


Periods?

Let's see how that proportion varies by book.

In [7]:
query = """
    for $book in //book
    let $bookname := $book/@base ! tokenize(., '[\.-]')[2]
    let $total := count($book//pc[. = (';', '.')])
    let $count := count($book//pc[.=(';')])
    let $percent := 100 * ($count div $total)
    order by $percent descending
    return  ``[`{$bookname}`: count=`{$count}`, percent=`{format-number($percent, "#.###")}` ]``  
"""

q.xquery(query)

1corinthians: count=107, percent=26.355 
romans: count=83, percent=22.802 
james: count=22, percent=20.952 
john: count=169, percent=18.799 
matthew: count=169, percent=17.441 
mark: count=111, percent=17.209 
galatians: count=19, percent=15.323 
luke: count=153, percent=15.194 
2corinthians: count=26, percent=13.0 
hebrews: count=18, percent=9.137 
acts: count=69, percent=8.949 
1peter: count=4, percent=6.897 
1thessalonians: count=2, percent=3.922 
1john: count=4, percent=3.738 
2thessalonians: count=1, percent=3.704 
2peter: count=1, percent=3.333 
colossians: count=1, percent=2.381 
revelation: count=8, percent=2.235 
ephesians: count=1, percent=1.695 
philippians: count=1, percent=1.613 
1timothy: count=0, percent=.0 
2timothy: count=0, percent=.0 
titus: count=0, percent=.0 
philemon: count=0, percent=.0 
2john: count=0, percent=.0 
3john: count=0, percent=.0 
jude: count=0, percent=.0 


### A list of questions marked with a question mark

Let's take a look at these questions so that we can attempt to classify them.  

In [8]:
q.find("//sentence[.//pc=';']")

Note that the sentence element in the Lowfat database does not correspond to sentences identified by punctuation.  For instance, a sentence element often ends with a semicolon and contains no period or question mark.  Also, a single sentence element may contain several questions, as shown in the following examples.

In [9]:
q.find("//sentence[count(.//pc[.=';']) >= 3]")

# Interrogative Pronouns

What are the interrogative pronouns?

In [10]:
query = "distinct-values(//w[@class='pron' and @type='interrogative']/@lemma)"
q.xquery(query)

τίς
πόσος
ποῖος


How many times is each interrogative pronoun used, and where?

## τίς

### τίς - all instances

In [11]:
query = "//w[@lemma='τίς' and @type='interrogative']"

In [12]:
q.count(query)

In [13]:
q.highlight(query)

### gender, case, and the meaning of τίς 

When asking 'who', Greek tends to use the masculine form τίς unless the question implies a particular gender for the answer.  When asking 'what', Greek tends to use the nominative form τί unless the question implies a particular gender for the answer. This can be seen in the distribution of glosses: τίς tends to be translated 'who' or 'whom', τί tends to be translated 'what', 'of what', 'for what', etc. τί can also mean 'why', and the phrases most commonly used to ask 'why' contain τί.

The following query looks at the distribution of glosses as a rough overview of the role of gender and case in the meaning of τίς.  This is a coarse measure, of course, and runs the risk of conflating the meaning of a word with its translation, but it is still indicative.

In [14]:
query = """
    for $gender in ('masculine', 'feminine', 'neuter')
    for $case in ('nominative', 'genitive', 'dative','accusative')
    let $w := //w[@lemma='τίς' and @gender=$gender and @case=$case]
    return 
      <div>
        <h2>{ $gender, $case }</h2>
        <ul>        
         {
            for $w in $w
            let $gloss := lower-case($w/@gloss)
            group by $gloss
            order by count($w) descending
            return <li>{ $gloss, count($w) }</li> 
         }
        </ul>
      </div>
"""

HTML(q._xquery(query))

### τίς - by gender

#### masculine

In [15]:
query = "//w[@lemma='τίς' and @type='interrogative' and @gender='masculine']"
q.count(query)

In [16]:
q.highlight(query)

#### feminine

In [17]:
query = "//w[@lemma='τίς' and @type='interrogative' and @gender='feminine']"
q.count(query)

In [18]:
q.highlight(query)

#### neuter

In [19]:
query = "//w[@lemma='τίς' and @type='interrogative' and @gender='neuter']"
q.count(query)

In [20]:
q.highlight(query)

### Indefinite τις

Note that the interrogative pronoun τίς is closely related to the indefinite pronoun τις. In the nominative and accusative they can be distinguished by accentuation; in the dative and genitive they can only be distinguished by usage.

In [21]:
query = "distinct-values(//w[@class='pron' and @type='indefinite']/@lemma)"
q.xquery(query)

τὶς


In [22]:
query = "//w[@class='pron' and @type='indefinite']"
q.highlight(query)

### τίς - by case

#### Nominative

In [23]:
query = "//w[@lemma='τίς' and @type='interrogative' and @case='nominative']"
q.highlight(query)

#### Genitive

In [24]:
query = "//w[@lemma='τίς' and @type='interrogative' and @case='genitive']"
q.highlight(query)

#### Dative

In [25]:
query = "//w[@lemma='τίς' and @type='interrogative' and @case='dative']"
q.highlight(query)

#### Accusative

In [26]:
query = "//w[@lemma='τίς' and @type='interrogative' and @case='accusative']"
q.highlight(query)

 ## τί

### τί - what?

In [27]:
q.highlight("//w[@lemma='τίς' and contains(@gloss,'what')]")

#### τί γάρ

In [28]:
q.highlight("//w[@lemma='γάρ']/following::wg[1][w[@lemma='τίς']]")

#### Τί οὖν

In [29]:
q.highlight("//w[@lemma='οὖν']/following::wg[1][w[@lemma='τίς']]")

#### τί ἐμοὶ καὶ σοί

In [30]:
q.highlight("//wg[w[@lemma='τίς']/following::w[1][@normalized='ἐμοί']]")

#### τί πρὸς ἡμᾶς

In [31]:
q.highlight("//wg[w[@lemma='τίς']/following::w[1][@normalized='πρός']]")

### τί - why?

In [32]:
q.highlight("//w[@lemma='τίς' and @gloss='why']")

#### διὰ τί

In [33]:
q.highlight("//wg[w[@lemma='διά']/following::w[1][@lemma='τίς']]")

#### ἱνατί

In [34]:
q.highlight("//wg[w[@lemma='ἵνα']/following::w[1][@lemma='τίς']]")

#### εἰς τί

In [ ]:
q.highlight("//wg[w[@lemma='εἰς']/following::w[1][@lemma='τίς']]")

#### τί ὅτι

In [ ]:
q.highlight("//wg[w[@lemma='τίς']/following::w[1][@lemma='ὅτι']]")

#### χάριν τίνος

In [ ]:
q.highlight("//wg[w[@lemma='χάριν']/following::w[1][@lemma='τίς']]")

### τί - who?

In [ ]:
q.highlight("//w[@lemma='τίς' and @gloss='who']")

## πόσος

In [ ]:
query = "//w[@lemma='πόσος' and @type='interrogative']"
q.count(query)

In [ ]:
q.highlight(query)

## ποῖος

In [ ]:
query = "//w[@lemma='ποῖος' and @type='interrogative']"
q.count(query)

In [ ]:
q.highlight(query)

# Interrogative Adjectives

In [ ]:
q.xquery("distinct-values(//w[@type='interrogative' and @class='adj']/@lemma)")

## ἡλίκος

In [ ]:
query= "//w[@type='interrogative' and @class='adj' and @lemma='ἡλίκος']"
q.count(query)

In [ ]:
q.highlight(query)

## πηλίκος

In [ ]:
query="//w[@type='interrogative' and @class='adj' and @lemma='πηλίκος']"
q.count(query)

In [ ]:
q.highlight(query)

## ὁποῖος

In [ ]:
query="//w[@type='interrogative' and @class='adj' and @lemma='ὁποῖος']"
q.count(query)

In [ ]:
q.highlight(query)

## ποταπός

In [ ]:
query = "//w[@type='interrogative' and @class='adj' and @lemma='ποταπός']"
q.count(query)

In [ ]:
q.highlight(query)

# Interrogative Adverbs

## πόθεν

In [ ]:
query="//w[@lemma='πόθεν' and @class='adv']"
q.count(query)

In [ ]:
q.highlight(query)

## πότε

In [ ]:
query="//w[@lemma='πότε' and @class='adv']"
q.count(query)

In [ ]:
q.highlight(query)

## ποῦ

In [ ]:
query="//w[@lemma='ποῦ' and @class='adv']"
q.count(query)

In [ ]:
q.highlight(query)

## πῶς

In [ ]:
def classes(w):
    q.xquery("distinct-values(//w[@lemma='"+w+"']/@class)")
    
classes("πῶς")

In [ ]:
query="//w[@lemma='πῶς' and @class='conj']"
q.count(query)

In [ ]:
q.highlight(query)

In [ ]:
query="//w[@lemma='πῶς' and @class='adv']"
q.count(query)

In [ ]:
q.highlight(query)

# Interrogative Particles

See Smyth, [QUESTIONS INTRODUCED BY INTERROGATIVE PARTICLES](http://www.perseus.tufts.edu/hopper/text?doc=Perseus%3Atext%3A1999.04.0007%3Apart%3D4%3Achapter%3D56%3Asection%3D154%3Asubsection%3D163)

## ἄρα

In [ ]:
classes("ἄρα")

In [ ]:
query="//w[@lemma='ἄρα' and @class='ptcl']"
q.count(query)

In [ ]:
q.highlight(query)

In [ ]:
query="//w[@lemma='ἄρα' and @class='conj']"
q.count(query)

In [ ]:
q.highlight(query)

## ἤ

In [ ]:
query = "//sentence[.//pc[.=';']//w[@lemma='ἤ']"
q.count(query)

In [ ]:
q.highlight(query)

In [ ]:
classes("ἤ")

In [ ]:
query = "//w[@lemma='ἤ' and @class='conj']"
q.count(query)

In [ ]:
q.highlight(query)

In [ ]:
query = "//w[@lemma='ἤ' and @class='ptcl']"
q.count(query)

In [ ]:
q.highlight(query)

## οὐ

In [ ]:
classes("οὐ")

In [ ]:
query = "//w[@lemma='οὐ' and @class='ptcl']"
q.count(query)

In [ ]:
q.highlight(query)

In [ ]:
query = "//w[@lemma='οὐ' and @class='adv']"
q.count(query)

In [ ]:
query = milestone("John") + query
q.highlight(query)

## μή

In [ ]:
classes("μή")

## οὐ μή

# Giving choices with ἢ

 # Tone of Voice

# TODO

Particles
